# Section 1
## make the table with preparation information

In [1]:
## Now need to add solution treatment, substrate_pretreat and post process info

# 1 if treatment is done and 0 if no treatment

#adding the hole mobility information. only adding hole_mobility not NAN. getting rid of NAN

import psycopg2
import pandas as pd
import numpy as np
import plotly.express as px

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

pgparams = {
    "host": "chbe-ofet-db.postgres.database.azure.com",
    "database": "ofetdb_v2",
    "user": "mg200_ofetdb",
    "password": "MGEROFETDB23!",
    "port": "5432",
}

def read_select_query(query):
    with psycopg2.connect(**pgparams) as conn:
        df = pd.read_sql_query(query, conn)
    return df

# SQL query to fetch the required data
query ='''
    SELECT
        s.sample_id,
        e.citation_type,
        e.meta as experiment_meta,
        sol.concentration as solution_concentration,
        sm_s.vol_frac as solvent_vol_frac,
        sv.pubchem_cid as solvent_pubchem_cid,
        sv.iupac_name as solvent_iupac_name,
        p.common_name as polymer_common_name,
        p.iupac_name as polymer_iupac_name,
        p.mw as polymer_mw,
        p.mn as polymer_mn,
        p.dispersity as polymer_dispersity,
        df.params as device_substrate_parameters,
        fd.deposition_type as film_deposition_type,
        fd.params as film_deposition_params,
        CAST(m.data -> 'hole_mobility' ->> 'value' AS FLOAT) AS hole_mobility,
        CASE WHEN op.solution_treatment_id IS NOT NULL THEN 1 ELSE 0 END AS Solution_treatment,
        CASE WHEN op.substrate_pretreat_id IS NOT NULL THEN 1 ELSE 0 END AS Substrate_pretreatment,
        CASE WHEN op.postprocess_id IS NOT NULL THEN 1 ELSE 0 END AS Post_Process
    FROM
        SAMPLE s
    JOIN
        EXPERIMENT_INFO e ON s.exp_id = e.exp_id
    LEFT JOIN
        OFET_PROCESS op ON s.process_id = op.process_id
    LEFT JOIN
        SOLUTION sol ON op.solution_id = sol.solution_id
    LEFT JOIN
        SOLUTION_MAKEUP_SOLVENT sm_s ON sol.solution_id = sm_s.solution_id
    LEFT JOIN
        SOLVENT sv ON sm_s.solvent_id = sv.pubchem_cid
    LEFT JOIN
        SOLUTION_MAKEUP_POLYMER sm_p ON sol.solution_id = sm_p.solution_id
    LEFT JOIN
        POLYMER p ON sm_p.polymer_id = p.polymer_id
    LEFT JOIN
        DEVICE_FABRICATION df ON op.device_fab_id = df.device_fab_id
    LEFT JOIN
        FILM_DEPOSITION fd ON op.film_deposition_id = fd.film_deposition_id
    LEFT JOIN
        MEASUREMENT m ON s.sample_id = m.sample_id
    WHERE
        sm_s.vol_frac = 1 AND
        sm_p.wt_frac = 1 AND
        m.measurement_type = 'transfer_curve' AND
        m.data -> 'hole_mobility' ->> 'value' IS NOT NULL;
'''


# Use the read_select_query function to execute the query
result_df = read_select_query(query)

# Display the resulting DataFrame
result_df

C:\Users\Myeongyeon Lee\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


sample_id citation_type  \
0            1    literature   
1            2    literature   
2            3    literature   
3            4    literature   
4            5    literature   
5            6    literature   
6            7    literature   
7            8    literature   
8            9    literature   
9           10    literature   
10          11    literature   
11          12    literature   
12          21    literature   
13          22    literature   
14          23    literature   
15          24    literature   
16          25    literature   
17          26    literature   
18          27    literature   
19          28    literature   
20          29    literature   
21          30    literature   
22          31    literature   
23          32    literature   
24          33    literature   
25          34    literature   
26          35    literature   
27          43    literature   
28          44    literature   
29          45    literature   
30          46    literature   
31          47    literature   
32          48    literature   
33          49    literature   
34          50    literature   
35          51    literature   
36          52    literature   
37          53    literature   
38          54    literature   
39          55    literature   
40          56    literature   
41          57    literature   
42          58    literature   
43          59    literature   
44          60    literature   
45          61    literature   
46          62    literature   
47          63    literature   
48          64    literature   
49          65    literature   
50          66    literature   
51          67    literature   
52          68    literature   
53          75    literature   
54          81    literature   
55          82    literature   
56          83    literature   
57          84    literature   
58          85    literature   
59          86    literature   
60          87    literature   
61          88    literature   
62          89    literature   
63          90    literature   
64          91    literature   
65          92    literature   
66          93    literature   
67          94    literature   
68          95    literature   
69          96    literature   
70          97    literature   
71          98    literature   
72          99    literature   
73         100    literature   
74         101    literature   
75         102    literature   
76         103    literature   
77         104    literature   
78         105    literature   
79         106    literature   
80         107    literature   
81         108    literature   
82         109    literature   
83         110    literature   
84         111    literature   
85         112    literature   
86         113    literature   
87         114    literature   
88         115    literature   
89         116    literature   
90         117    literature   
91         118    literature   
92         119    literature   
93         120    literature   
94         121    literature   
95         122    literature   
96         123    literature   
97         124    literature   
98         125    literature   
99         126    literature   
100        127    literature   
101        128    literature   
102        129    literature   
103        130    literature   
104        131    literature   
105        132    literature   
106        133    literature   
107        134    literature   
108        135    literature   
109        136    laboratory   
110        137    laboratory   
111        138    laboratory   
112        139    laboratory   
113        140    laboratory   
114        141    laboratory   
115        142    laboratory   
116        143    laboratory   
117        190    literature   
118        144    laboratory   
119        149    laboratory   
120        154    laboratory   
121        159    laboratory   
122        160    laboratory   
123        161    laboratory   
124  

In [2]:
 #unpacking the information stored in device_substrate_parameters

import pandas as pd
from pandas import json_normalize



# # Extract the 'device_substrate_parameters' column and normalize it
params_df = json_normalize(result_df['device_substrate_parameters'])

# # Concatenate the original DataFrame with the new 'params_df'
result_df = pd.concat([result_df, params_df], axis=1)

# # Drop the original 'device_substrate_parameters' column
result_df = result_df.drop('device_substrate_parameters', axis=1)

# # Display the resulting DataFrame
result_df

sample_id citation_type  \
0            1    literature   
1            2    literature   
2            3    literature   
3            4    literature   
4            5    literature   
5            6    literature   
6            7    literature   
7            8    literature   
8            9    literature   
9           10    literature   
10          11    literature   
11          12    literature   
12          21    literature   
13          22    literature   
14          23    literature   
15          24    literature   
16          25    literature   
17          26    literature   
18          27    literature   
19          28    literature   
20          29    literature   
21          30    literature   
22          31    literature   
23          32    literature   
24          33    literature   
25          34    literature   
26          35    literature   
27          43    literature   
28          44    literature   
29          45    literature   
30          46    literature   
31          47    literature   
32          48    literature   
33          49    literature   
34          50    literature   
35          51    literature   
36          52    literature   
37          53    literature   
38          54    literature   
39          55    literature   
40          56    literature   
41          57    literature   
42          58    literature   
43          59    literature   
44          60    literature   
45          61    literature   
46          62    literature   
47          63    literature   
48          64    literature   
49          65    literature   
50          66    literature   
51          67    literature   
52          68    literature   
53          75    literature   
54          81    literature   
55          82    literature   
56          83    literature   
57          84    literature   
58          85    literature   
59          86    literature   
60          87    literature   
61          88    literature   
62          89    literature   
63          90    literature   
64          91    literature   
65          92    literature   
66          93    literature   
67          94    literature   
68          95    literature   
69          96    literature   
70          97    literature   
71          98    literature   
72          99    literature   
73         100    literature   
74         101    literature   
75         102    literature   
76         103    literature   
77         104    literature   
78         105    literature   
79         106    literature   
80         107    literature   
81         108    literature   
82         109    literature   
83         110    literature   
84         111    literature   
85         112    literature   
86         113    literature   
87         114    literature   
88         115    literature   
89         116    literature   
90         117    literature   
91         118    literature   
92         119    literature   
93         120    literature   
94         121    literature   
95         122    literature   
96         123    literature   
97         124    literature   
98         125    literature   
99         126    literature   
100        127    literature   
101        128    literature   
102        129    literature   
103        130    literature   
104        131    literature   
105        132    literature   
106        133    literature   
107        134    literature   
108        135    literature   
109        136    laboratory   
110        137    laboratory   
111        138    laboratory   
112        139    laboratory   
113        140    laboratory   
114        141    laboratory   
115        142    laboratory   
116        143    laboratory   
117        190    literature   
118        144    laboratory   
119        149    laboratory   
120        154    laboratory   
121        159    laboratory   
122        160    laboratory   
123        161    laboratory   
124  

In [3]:

# Drop unnecessary columns that won't be used for modeling
columns_to_drop = ['film_deposition_params', 'citation_type', 'experiment_meta', 'solvent_vol_frac', 'solvent_iupac_name', 'polymer_iupac_name', 'dielectric_material_2', 'dielectric_thickness_2', 'dielectric_1_material', 'dielectric_1_thickness', 'substrate_material']
result_df = result_df.drop(columns=columns_to_drop)

# Display the resulting DataFrame
result_df


sample_id  solution_concentration  solvent_pubchem_cid  \
0            1                   4.000                 7964   
1            2                   4.000                 7964   
2            3                   4.000                 7964   
3            4                   4.000                 7964   
4            5                   4.000                 7964   
5            6                   4.000                 7964   
6            7                   4.000                 7964   
7            8                   4.000                 7964   
8            9                   4.000                 7964   
9           10                   4.000                 7964   
10          11                   4.000                 7964   
11          12                   5.000                 6212   
12          21                   5.000                 7964   
13          22                   5.000                 7964   
14          23                   5.000                 7964   
15          24                   5.000                 7964   
16          25                   5.000                 7964   
17          26                   5.000                 7964   
18          27                   5.000                 7964   
19          28                   5.000                 7964   
20          29                   5.000                 7964   
21          30                   5.000                 7964   
22          31                   5.000                 7964   
23          32                   5.000                 7964   
24          33                   5.000                 7964   
25          34                   5.000                 7964   
26          35                   4.000                 7239   
27          43                   6.500                 6212   
28          44                   6.500                 6212   
29          45                   6.500                 6212   
30          46                   6.500                 6212   
31          47                   6.500                 6212   
32          48                   6.500                 6212   
33          49                   6.500                 6212   
34          50                   6.500                 6212   
35          51                   3.000                 7239   
36          52                   3.000                 7239   
37          53                   7.000                 7239   
38          54                   7.000                 7239   
39          55                   6.500                 6212   
40          56                   1.600                 6212   
41          57                   1.600                 6212   
42          58                   0.500                 6212   
43          59                   0.750                 6212   
44          60                   1.000                 6212   
45          61                   2.000                 6212   
46          62                   5.000                 6212   
47          63                   0.500                 6212   
48          64                   0.750                 6212   
49          65                   1.000                 6212   
50          66                   2.000                 6212   
51          67                   5.000                 6212   
52          68                   2.000                 7239   
53          75                   4.000                 6212   
54          81                   5.000                 6212   
55          82                   5.000                 6212   
56          83                   5.000                 6212   
57          84                   7.000                 6212   
58          85                   8.500                 6212   
59          86                  10.000                 6212   
60          87                  12.000                 6212   
61          88                  14.000                 6212   
62          89                  16.0

In [4]:
# List of columns to one-hot encode
columns_to_one_hot_encode = ['film_deposition_type', 'gate_material', 'dielectric_material', 'electrode_configuration']

# Perform one-hot encoding
result_df = pd.get_dummies(result_df, columns=columns_to_one_hot_encode)

# Display the resulting DataFrame with one-hot encoding
result_df


sample_id  solution_concentration  solvent_pubchem_cid  \
0            1                   4.000                 7964   
1            2                   4.000                 7964   
2            3                   4.000                 7964   
3            4                   4.000                 7964   
4            5                   4.000                 7964   
5            6                   4.000                 7964   
6            7                   4.000                 7964   
7            8                   4.000                 7964   
8            9                   4.000                 7964   
9           10                   4.000                 7964   
10          11                   4.000                 7964   
11          12                   5.000                 6212   
12          21                   5.000                 7964   
13          22                   5.000                 7964   
14          23                   5.000                 7964   
15          24                   5.000                 7964   
16          25                   5.000                 7964   
17          26                   5.000                 7964   
18          27                   5.000                 7964   
19          28                   5.000                 7964   
20          29                   5.000                 7964   
21          30                   5.000                 7964   
22          31                   5.000                 7964   
23          32                   5.000                 7964   
24          33                   5.000                 7964   
25          34                   5.000                 7964   
26          35                   4.000                 7239   
27          43                   6.500                 6212   
28          44                   6.500                 6212   
29          45                   6.500                 6212   
30          46                   6.500                 6212   
31          47                   6.500                 6212   
32          48                   6.500                 6212   
33          49                   6.500                 6212   
34          50                   6.500                 6212   
35          51                   3.000                 7239   
36          52                   3.000                 7239   
37          53                   7.000                 7239   
38          54                   7.000                 7239   
39          55                   6.500                 6212   
40          56                   1.600                 6212   
41          57                   1.600                 6212   
42          58                   0.500                 6212   
43          59                   0.750                 6212   
44          60                   1.000                 6212   
45          61                   2.000                 6212   
46          62                   5.000                 6212   
47          63                   0.500                 6212   
48          64                   0.750                 6212   
49          65                   1.000                 6212   
50          66                   2.000                 6212   
51          67                   5.000                 6212   
52          68                   2.000                 7239   
53          75                   4.000                 6212   
54          81                   5.000                 6212   
55          82                   5.000                 6212   
56          83                   5.000                 6212   
57          84                   7.000                 6212   
58          85                   8.500                 6212   
59          86                  10.000                 6212   
60          87                  12.000                 6212   
61          88                  14.000                 6212   
62          89                  16.0

In [5]:
column_names = result_df.columns
print(column_names)

Index(['sample_id', 'solution_concentration', 'solvent_pubchem_cid',
       'polymer_common_name', 'polymer_mw', 'polymer_mn', 'polymer_dispersity',
       'hole_mobility', 'solution_treatment', 'substrate_pretreatment',
       'post_process', 'channel_width', 'channel_length',
       'dielectric_thickness', 'film_deposition_type_Dip Coating',
       'film_deposition_type_blade', 'film_deposition_type_dip',
       'film_deposition_type_drop', 'film_deposition_type_inkjet',
       'film_deposition_type_shear', 'film_deposition_type_spin',
       'film_deposition_type_wire', 'gate_material_Al', 'gate_material_Au',
       'gate_material_PEDOT:PSS', 'gate_material_PET', 'gate_material_Si',
       'gate_material_glass', 'gate_material_n-doped Si',
       'gate_material_p-doped Si', 'dielectric_material_6FDA-DABC',
       'dielectric_material_CYTOP', 'dielectric_material_PAN',
       'dielectric_material_PMMA', 'dielectric_material_PTrFE',
       'dielectric_material_PVP', 'dielectric_materi

In [6]:

#consolidating gate material columns
gate_material_Si_to_consolidate = ['gate_material_n-doped Si', 'gate_material_Si','gate_material_p-doped Si']
gate_material_other_to_consolidate = ['gate_material_Al', 'gate_material_Au', 'gate_material_PEDOT:PSS', 'gate_material_PET','gate_material_glass']
# Create new columns
result_df['gate_material_Si'] = result_df[gate_material_Si_to_consolidate].max(axis=1)
result_df['gate_material_Other'] = result_df[gate_material_other_to_consolidate].max(axis=1)
# Drop the original columns
result_df.drop(columns=gate_material_Si_to_consolidate, inplace=True)
result_df.drop(columns=gate_material_other_to_consolidate, inplace=True)


#consolidating coating columns
MGC_columns_to_consolidate = ['film_deposition_type_Dip Coating',
                           'film_deposition_type_blade',
                           'film_deposition_type_dip',
                           'film_deposition_type_inkjet',
                           'film_deposition_type_shear',
                           'film_deposition_type_wire']
# Create new columns
result_df['film_deposition_type_MGC'] = result_df[MGC_columns_to_consolidate].max(axis=1)
# Drop the original columns
result_df.drop(columns=MGC_columns_to_consolidate, inplace=True)


#consolidating dielectric columns
dielectric_material_columns_to_consolidate = ['dielectric_material_6FDA-DABC',
       'dielectric_material_CYTOP', 'dielectric_material_PAN',
       'dielectric_material_PMMA', 'dielectric_material_PTrFE',
       'dielectric_material_PVP', 'dielectric_material_Shellac',
       'dielectric_material_Si3N4']
# Create new columns
result_df['dielectric_material_other'] = result_df[dielectric_material_columns_to_consolidate].max(axis=1)
# Drop the original columns
result_df.drop(columns=dielectric_material_columns_to_consolidate, inplace=True)


In [7]:
result_df

sample_id  solution_concentration  solvent_pubchem_cid  \
0            1                   4.000                 7964   
1            2                   4.000                 7964   
2            3                   4.000                 7964   
3            4                   4.000                 7964   
4            5                   4.000                 7964   
5            6                   4.000                 7964   
6            7                   4.000                 7964   
7            8                   4.000                 7964   
8            9                   4.000                 7964   
9           10                   4.000                 7964   
10          11                   4.000                 7964   
11          12                   5.000                 6212   
12          21                   5.000                 7964   
13          22                   5.000                 7964   
14          23                   5.000                 7964   
15          24                   5.000                 7964   
16          25                   5.000                 7964   
17          26                   5.000                 7964   
18          27                   5.000                 7964   
19          28                   5.000                 7964   
20          29                   5.000                 7964   
21          30                   5.000                 7964   
22          31                   5.000                 7964   
23          32                   5.000                 7964   
24          33                   5.000                 7964   
25          34                   5.000                 7964   
26          35                   4.000                 7239   
27          43                   6.500                 6212   
28          44                   6.500                 6212   
29          45                   6.500                 6212   
30          46                   6.500                 6212   
31          47                   6.500                 6212   
32          48                   6.500                 6212   
33          49                   6.500                 6212   
34          50                   6.500                 6212   
35          51                   3.000                 7239   
36          52                   3.000                 7239   
37          53                   7.000                 7239   
38          54                   7.000                 7239   
39          55                   6.500                 6212   
40          56                   1.600                 6212   
41          57                   1.600                 6212   
42          58                   0.500                 6212   
43          59                   0.750                 6212   
44          60                   1.000                 6212   
45          61                   2.000                 6212   
46          62                   5.000                 6212   
47          63                   0.500                 6212   
48          64                   0.750                 6212   
49          65                   1.000                 6212   
50          66                   2.000                 6212   
51          67                   5.000                 6212   
52          68                   2.000                 7239   
53          75                   4.000                 6212   
54          81                   5.000                 6212   
55          82                   5.000                 6212   
56          83                   5.000                 6212   
57          84                   7.000                 6212   
58          85                   8.500                 6212   
59          86                  10.000                 6212   
60          87                  12.000                 6212   
61          88                  14.000                 6212   
62          89                  16.0

In [8]:
## replacing the pubchem_cid with solvent boiling point

# Get unique PubChem CIDs from the 'solvent_pubchem_cid' column
unique_pubchem_cids = result_df['solvent_pubchem_cid'].unique()

# Display the unique PubChem CIDs
print(unique_pubchem_cids)



[ 7964  6212  7239  6591  7809 13229    13  8030  1140  7501   241  6344
  7503]


In [9]:
# Dictionary mapping PubChem CIDs to boiling points
boiling_point_dict = {
    7964: 132,
    6212: 62,
    7239: 180.1,
    6591: 146,
    7809: 138,
    13229: 238,
    13: 213,
    8030: 84,
    1140: 111,
    7501: 145,
    241: 80,
    6344: 40,
    7503: 179
}

# Add a new column "solvent_boiling_point" based on PubChem CIDs
result_df['solvent_boiling_point'] = result_df['solvent_pubchem_cid'].map(boiling_point_dict)


# Drop unnecessary columns that won't be used for modeling
columns_to_drop = ['solvent_pubchem_cid']
result_df = result_df.drop(columns=columns_to_drop)

# Display the resulting DataFrame
result_df


sample_id  solution_concentration polymer_common_name   polymer_mw  \
0            1                   4.000             DPP-DTT     299.0000   
1            2                   4.000             DPP-DTT     299.0000   
2            3                   4.000             DPP-DTT     299.0000   
3            4                   4.000             DPP-DTT     299.0000   
4            5                   4.000             DPP-DTT     299.0000   
5            6                   4.000             DPP-DTT     299.0000   
6            7                   4.000             DPP-DTT     299.0000   
7            8                   4.000             DPP-DTT     299.0000   
8            9                   4.000             DPP-DTT     299.0000   
9           10                   4.000             DPP-DTT     299.0000   
10          11                   4.000             DPP-DTT     299.0000   
11          12                   5.000             DPP-DTT     292.2000   
12          21                   5.000             DPP-DTT      91.0000   
13          22                   5.000             DPP-DTT     344.0000   
14          23                   5.000             DPP-DTT     501.0000   
15          24                   5.000             DPP-DTT     501.0000   
16          25                   5.000             DPP-DTT     501.0000   
17          26                   5.000             DPP-DTT     501.0000   
18          27                   5.000             DPP-DTT     501.0000   
19          28                   5.000             DPP-DTT     501.0000   
20          29                   5.000             DPP-DTT     501.0000   
21          30                   5.000             DPP-DTT     501.0000   
22          31                   5.000             DPP-DTT     501.0000   
23          32                   5.000             DPP-DTT     501.0000   
24          33                   5.000             DPP-DTT     501.0000   
25          34                   5.000             DPP-DTT     501.0000   
26          35                   4.000             DPP-DTT     199.0000   
27          43                   6.500             DPP-DTT      91.0000   
28          44                   6.500             DPP-DTT      91.0000   
29          45                   6.500             DPP-DTT      91.0000   
30          46                   6.500             DPP-DTT      91.0000   
31          47                   6.500             DPP-DTT      91.0000   
32          48                   6.500             DPP-DTT      91.0000   
33          49                   6.500             DPP-DTT      91.0000   
34          50                   6.500             DPP-DTT      91.0000   
35          51                   3.000             DPP-DTT     290.0000   
36          52                   3.000             DPP-DTT     290.0000   
37          53                   7.000             DPP-DTT     290.0000   
38          54                   7.000             DPP-DTT     290.0000   
39          55                   6.500             DPP-DTT     100.0000   
40          56                   1.600             DPP-DTT     279.0000   
41          57                   1.600             DPP-DTT     279.0000   
42          58                   0.500             DPP-DTT     102.0000   
43          59                   0.750             DPP-DTT     102.0000   
44          60                   1.000             DPP-DTT     102.0000   
45          61                   2.000             DPP-DTT     102.0000   
46          62                   5.000             DPP-DTT     102.0000   
47          63                   0.500             DPP-DTT     102.0000   
48          64                   0.750             DPP-DTT     102.0000   
49          65                   1.000             DPP-DTT     102.0000   
50          66                   2.000             DPP-DTT     102.0000   
51          67                   5.000             DPP-DTT     102.0000   
52          68                

# Section 2
## make the table with process paramter

In [10]:
##consider processing with order
query = '''
   SELECT
        s.sample_id,
        spstep.params AS params,
        MAX(CASE WHEN spstep.treatment_type = 'sam' THEN 1 ELSE 0 END) AS treatment_type_sam,
        MAX(CASE WHEN spstep.treatment_type = 'plasma_treatment' THEN 1 ELSE 0 END) AS treatment_type_plasma,
        MAX(CASE WHEN spstep.treatment_type = 'uv_ozone' THEN 1 ELSE 0 END) AS treatment_type_uv_ozone,
        
        CASE WHEN spstep.params ->> 'iupac_name' = 'water' THEN 1 ELSE 0 END AS is_water_treatment,
        CASE WHEN spstep.params ->> 'iupac_name' = 'isopropanol' THEN 1 ELSE 0 END AS is_isopropanol_treatment,
        CASE WHEN spstep.params ->> 'iupac_name' = 'ethanol' THEN 1 ELSE 0 END AS is_ethanol_treatment,
        CASE WHEN spstep.params ->> 'iupac_name' = 'acetone' THEN 1 ELSE 0 END AS is_acetone_treatment,
        CASE WHEN spstep.params ->> 'iupac_name' = 'methanol' THEN 1 ELSE 0 END AS is_methanol_treatment,
        CASE WHEN spstep.params ->> 'iupac_name' = 'piranha solution' THEN 1 ELSE 0 END AS is_piranha_treatment,
        CASE WHEN spstep.params ->> 'iupac_name' = 'PEIE' THEN 1 ELSE 0 END AS is_PEIE_treatment,
        CASE WHEN spstep.params ->> 'iupac_name' = 'RCA' THEN 1 ELSE 0 END AS is_RCA_treatment,
        CASE WHEN spstep.params ->> 'iupac_name' = 'toluene' THEN 1 ELSE 0 END AS is_toluene_treatment,
        
        
        MAX(CASE WHEN ststep.treatment_type = 'poor_solvent' THEN 1 ELSE 0 END) AS solution_treatment_poor_solvent,
        MAX(CASE WHEN ststep.treatment_type = 'aging' THEN 1 ELSE 0 END) AS solution_treatment_aging,
        MAX(CASE WHEN ststep.treatment_type = 'sonication' THEN 1 ELSE 0 END) AS solution_treatment_sonication,
        MAX(CASE WHEN ststep.treatment_type = 'mixing' THEN 1 ELSE 0 END) AS solution_treatment_mixing,
        MAX(CASE WHEN ststep.treatment_type = 'uv_irradiation' THEN 1 ELSE 0 END) AS solution_treatment_uv_irradiation,
    
    
        MAX(CASE WHEN ppstep.treatment_type = 'annealing' THEN 1 ELSE 0 END) AS post_process_annealing,
        MAX(CASE WHEN ppstep.treatment_type = 'drying' THEN 1 ELSE 0 END) AS  post_process_drying,
        MAX(CASE WHEN ppstep.treatment_type = 'chemical_treat' THEN 1 ELSE 0 END) AS post_process_chemical
        
       
    -- Add more similar lines for other treatment types as needed
    
    
     FROM
        SAMPLE s
    JOIN
        OFET_PROCESS of ON s.process_id = of.process_id
    LEFT JOIN 
        SUBSTRATE_PRETREAT_ORDER spo ON of.substrate_pretreat_id = spo.substrate_pretreat_id
    LEFT JOIN
        SUBSTRATE_PRETREAT_STEP spstep ON spstep.substrate_pretreat_step_id = spo.substrate_pretreat_step_id
    LEFT JOIN
        SOLUTION_TREATMENT_ORDER sto ON of.solution_treatment_id = sto.solution_treatment_id
    LEFT JOIN
        SOLUTION_TREATMENT_STEP ststep ON sto.solution_treatment_step_id = ststep.solution_treatment_step_id
    LEFT JOIN
        POSTPROCESS_ORDER ppo ON of.postprocess_id = ppo.postprocess_id
    LEFT JOIN
        POSTPROCESS_STEP ppstep ON ppo.postprocess_step_id = ppstep.postprocess_step_id
    GROUP BY
        s.sample_id,
        spstep.params
    ORDER BY
        s.sample_id ASC;

'''


# Use the read_select_query function to execute the query
result_df_chem1= read_select_query(query)

result_df_chem1  

#keep substrate_treatment_type_sam, aging, sonication,uv_irrad,pp_annealing. remove everything else

C:\Users\Myeongyeon Lee\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


sample_id                                             params  \
0             1                                               None   
1             2  {'sam_name': 'MTS', 'iupac_name': 'methyltrich...   
2             3  {'sam_name': 'PTS', 'iupac_name': 'phenyltrich...   
3             4  {'sam_name': 'OTS-8', 'iupac_name': 'octyltric...   
4             5  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
5             6  {'sam_name': 'MTS', 'iupac_name': 'methyltrich...   
6             6  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
7             7  {'sam_name': 'MTS', 'iupac_name': 'methyltrich...   
8             7  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
9             8  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
10            8  {'sam_name': 'PTS', 'iupac_name': 'phenyltrich...   
11            9  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
12            9  {'sam_name': 'PTS', 'iupac_name': 'phenyltrich...   
13           10  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
14           10  {'sam_name': 'OTS-8', 'iupac_name': 'octyltric...   
15           11  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
16           11  {'sam_name': 'OTS-8', 'iupac_name': 'octyltric...   
17           12                                               None   
18           13                                               None   
19           14                                               None   
20           15                                               None   
21           16                                               None   
22           17                                               None   
23           18                                               None   
24           19                                               None   
25           20                                               None   
26           21                                               None   
27           22                                               None   
28           23                                               None   
29           24  {'sam_name': 'OTS-8', 'iupac_name': 'octyltric...   
30           25  {'sam_name': 'OTS-8', 'iupac_name': 'octyltric...   
31           26  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
32           27  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
33           28  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
34           29  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
35           30  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
36           31  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
37           32  {'sam_name': 'OTS-8', 'iupac_name': 'octyltric...   
38           33  {'sam_name': 'OTS-8', 'iupac_name': 'octyltric...   
39           34  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
40           35  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
41           36  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
42           37  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
43           38  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
44           39  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
45           40  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
46           41  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
47           42  {'sam_name': 'OTS-18', 'iupac_name': 'octadecy...   
48           43                                               None   
49           44                                               None   
50           45                                               None   
51           46                                               None   
52           47                                               None   
53           48                                               None   
54           49                                               None   
55           50                                               None   
56           51 

In [11]:
#Combining dulicated sample_id info
result_df_chem1 = result_df_chem1.drop(columns='params')
result_df_chem1 = result_df_chem1.groupby('sample_id').max()
result_df_chem1

treatment_type_sam  treatment_type_plasma  treatment_type_uv_ozone  \
sample_id                                                                       
1                           0                      0                        0   
2                           1                      0                        0   
3                           1                      0                        0   
4                           1                      0                        0   
5                           1                      0                        0   
6                           1                      0                        0   
7                           1                      0                        0   
8                           1                      0                        0   
9                           1                      0                        0   
10                          1                      0                        0   
11                          1                      0                        0   
12                          0                      0                        0   
13                          0                      0                        0   
14                          0                      0                        0   
15                          0                      0                        0   
16                          0                      0                        0   
17                          0                      0                        0   
18                          0                      0                        0   
19                          0                      0                        0   
20                          0                      0                        0   
21                          0                      0                        0   
22                          0                      0                        0   
23                          0                      0                        0   
24                          1                      0                        0   
25                          1                      0                        0   
26                          1                      0                        0   
27                          1                      0                        0   
28                          1                      0                        0   
29                          1                      0                        0   
30                          1                      0                        0   
31                          1                      0                        0   
32                          1                      0                        0   
33                          1                      0                        0   
34                          1                      0                        0   
35                          1                      0                        0   
36                          1                      0                        0   
37                          1                      0                        0   
38                          1                      0                        0   
39                          1                      0                        0   
40                          1                      0                        0   
41                          1                      0                        0   
42                          1                      0                        0   
43                          0                      0                        0   
44                          0                      0                        0   
45                          0                      0                        0   
46                          0                      0                        0   
47                          0                      0                        0   
48                          0             

# Section 3
## Combining two tables

In [12]:
combined_df = pd.merge(result_df, result_df_chem1, on="sample_id", how="inner")

In [13]:
combined_df

In [ ]:
combined_column_names = combined_df.columns
print(combined_column_names)

In [ ]:
combined_columns_to_drop = ['treatment_type_plasma','treatment_type_uv_ozone', 'is_water_treatment',
                          'is_isopropanol_treatment', 'is_ethanol_treatment','is_acetone_treatment',
                          'is_methanol_treatment', 'is_piranha_treatment','is_peie_treatment',
                          'is_rca_treatment', 'is_toluene_treatment','solution_treatment_poor_solvent',
                          'solution_treatment_mixing','post_process_drying', 'post_process_chemical']
combined_df = combined_df.drop(columns=combined_columns_to_drop)
combined_df

# P3HT Modeling

In [ ]:
combined_df_P3HT = combined_df[combined_df['polymer_common_name'] == 'P3HT']
combined_df_P3HT

In [ ]:
num_rows, num_columns = combined_df_P3HT.shape
print(f"Number of rows: {num_rows}")
print(f"Number of columns: {num_columns}")

In [ ]:
print(combined_df_P3HT.isna().sum(axis=0))
print('Total observations: {}'.format(combined_df_P3HT.shape[0]))
print('Total features: {}'.format(combined_df_P3HT.shape[1]))

In [ ]:
combined_df_P3HT = combined_df_P3HT.drop(['dielectric_material_other', 'gate_material_Other', 'electrode_configuration_TGBC', 'dielectric_thickness'], axis=1)
num_rows, num_columns = combined_df_P3HT.shape
print(f"Number of rows: {num_rows}")
print(f"Number of columns: {num_columns}")

In [ ]:
combined_df_P3HT.to_excel('combined_df_P3HT.xlsx', index=True, header=True)

# DPP-DTT Modeling

In [ ]:
combined_df_DPP_DTT = combined_df[combined_df['polymer_common_name'] == 'DPP-DTT']
combined_df_DPP_DTT

In [ ]:
num_rows, num_columns = combined_df_DPP_DTT.shape
print(f"Number of rows: {num_rows}")
print(f"Number of columns: {num_columns}")

In [ ]:
print(combined_df_DPP_DTT.isna().sum(axis=0))
print('Total observations: {}'.format(combined_df_DPP_DTT.shape[0]))
print('Total features: {}'.format(combined_df_DPP_DTT.shape[1]))


In [ ]:
combined_df_DPP_DTT = combined_df_DPP_DTT.drop(['film_deposition_type_drop', 'dielectric_thickness'], axis=1)
num_rows, num_columns = combined_df_DPP_DTT.shape
print(f"Number of rows: {num_rows}")
print(f"Number of columns: {num_columns}")

In [ ]:
combined_df_DPP_DTT.to_excel('combined_df_DPP_DTT.xlsx', index=True, header=True)